In [21]:
import geopandas as gpd
import pandas as pd
import matplotlib.pyplot as plt
from pathlib import Path
import matplotlib.font_manager as fm 
from matplotlib.patches import Patch

In [22]:
# Set environment options
gpd.options.io_engine = "pyogrio"

In [23]:
# Load the "Jost" font needed for this plot
font_dir = ['./source/Jost_Font/']  # Font is located in Jost_Font folder
for font in fm.findSystemFonts(font_dir):
    fm.fontManager.addfont(font)

In [24]:
# Load datasets needed for this plot

# Voter participation data
data = pd.read_csv("./source/NRW2023-wahlbeteiligung.csv", sep=';')

# Swiss map boundaries data
border_folder = Path("./source/boundaries")
map_canton = gpd.read_file(str(border_folder / "k4k23.shx"))
map_municipality = gpd.read_file(str(border_folder / "k4g23.shx"))

In [25]:
# Adjust data to needs of this plot

# Only use voter data of municipalities
data_municipality = data[data["ebene_resultat"].isin(["Gemeinde"])]
# Add a column with canton abbreviations for annotations
data_municipality["kanton_abbr"] = data_municipality["kanton_nummer"].map({1: "ZH", 2: "BE", 3: "LU", 4: "UR", 5: "SZ", 6: "OW", 7: "NW", 8: "GL", 9: "ZG", 10: "FR", 11: "SO", 12: "BS", 13: "BL", 14: "SH", 15: "AR", 16: "AI", 17: "SG", 18: "GR", 19: "AG", 20: "TG", 21: "TI", 22: "VD", 23: "VS", 24: "NE", 25: "GE", 26: "JU",})
# Rename the municipality name column
map_municipality = map_municipality.rename(columns={'GMDNAME': 'gemeinde_bezeichnung'})
# Merge the voter data and the map border data
map_municipality = map_municipality.merge(data_municipality, on="gemeinde_bezeichnung")
# Add a column with the density of voters in voters per square kilometer
map_municipality["voter_per_qkm2"] = map_municipality["wahlberechtigte"].astype(int) / (map_municipality["AREA_HA"].astype(float) / 100)
# Extract the float value of average participation in Switzerland
avg_participation = data["wahlbeteiligung"][0]

C:\Users\dave_\AppData\Local\Temp\ipykernel_11320\3082617585.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data_municipality["kanton_abbr"] = data_municipality["kanton_nummer"].map({1: "ZH", 2: "BE", 3: "LU", 4: "UR", 5: "SZ", 6: "OW", 7: "NW", 8: "GL", 9: "ZG", 10: "FR", 11: "SO", 12: "BS", 13: "BL", 14: "SH", 15: "AR", 16: "AI", 17: "SG", 18: "GR", 19: "AG", 20: "TG", 21: "TI", 22: "VD", 23: "VS", 24: "NE", 25: "GE", 26: "JU",})


In [26]:
# Create colormap
from matplotlib.colors import LinearSegmentedColormap

cmap = LinearSegmentedColormap.from_list(name="my_cmap", 
                                                colors=["#5e3c99", "#b2abd2", "white", '#fdb863','#e66101'], N=6)

In [27]:
# Define legend elements for values lower than average
legend_elements_negative = [
       Patch(facecolor='#5e3c99', label='> 16%'),
       Patch(facecolor='#a195c7', label='8—16%'),
       Patch(facecolor='#eebdbd', label='0—8%'),
]

# Define legend elements for values above average
legend_elements_positive = [
       Patch(facecolor='#e66101', label='> 16%'),
       Patch(facecolor='#f8a74f', label='8—16%'),
       Patch(facecolor='#fee3c1', label='0—8%'),
]

# Define look and feel of legend
legend_kwargs = {
       'prop': {'family': 'Jost', 'size': 18, 'weight': 'regular'}, 
       'labelcolor': 'dimgrey', 
       'framealpha': 0, 
       'labelspacing': 0.1, 
       'handlelength': 1.5, 
       'handleheight': 1, 
       'handletextpad': 0.4,
}


In [28]:
# Prepare annotation items -> highest, lowest without appenzell innerrhoden, lowest overall voting participation municipalities
sorted_by_participation = map_municipality.sort_values('wahlbeteiligung')
participation_without_ai = sorted_by_participation.loc[sorted_by_participation.KTNR != 16]

highest = sorted_by_participation.tail(1)
lowest_overall = sorted_by_participation.head(1)
lowest_without_ai = participation_without_ai.head(1)

annotation_items = {
    f'{highest["gemeinde_bezeichnung"].values[0]}, {highest["kanton_abbr"].values[0]}': [highest, (0.55, 0.1)],
    f'{lowest_overall["gemeinde_bezeichnung"].values[0]}, {lowest_overall["kanton_abbr"].values[0]}': [lowest_overall, (0.9, 0.9)],
    f'{lowest_without_ai["gemeinde_bezeichnung"].values[0]}, {lowest_without_ai["kanton_abbr"].values[0]}': [lowest_without_ai, (0.1, 0.85)]
}

# Define look and feel of annotation arrows
arrowprops = {
       'arrowstyle': 'Simple',
       'edgecolor': 'white',
       'facecolor': 'black',
       'linewidth': 1.5,
}

In [29]:
# Draw annotation items
def do_annotations(axis):
    for key, item in annotation_items.items():
        axis.annotate(
            key,
            xy=(item[0]['geometry'].centroid.x, item[0]['geometry'].centroid.y), xycoords='data',
            xytext=item[1], textcoords='axes fraction',
            size=30, va="center", ha="center",
            arrowprops={'connectionstyle': "arc3,rad=-0.2", **arrowprops},
            fontproperties={'family': 'Jost', 'size': 27, 'weight': 'semibold'}
        )
        
        text_x = item[1][0]
        text_y = item[1][1]
        text_y = text_y + 0.025 if text_y >= 0.5 else text_y - 0.025
        municipality_participation = item[0]['wahlbeteiligung'].values[0]
        participation_difference = municipality_participation - avg_participation
        color = '#e66101' if participation_difference >= 0 else '#5e3c99'
        axis.text(text_x - 0.02, text_y, f"{municipality_participation:.1f}%", fontproperties={'family': 'Jost', 'size': 20, 'weight': 'regular'}, horizontalalignment='center', verticalalignment='center', transform=axis.transAxes)
        axis.text(text_x + 0.02, text_y, f"({'+' if participation_difference >= 0 else '–'}{abs(municipality_participation - avg_participation):.1f}%)", color=color, fontproperties={'family': 'Jost', 'size': 20, 'weight': 'semibold'}, horizontalalignment='center', verticalalignment='center', transform=axis.transAxes)

In [30]:
# Create figure and axis
f, ax = plt.subplots(figsize=(36, 27), dpi=300)
p = map_municipality.plot(column="wahlbeteiligung", ax=ax, linewidth=1, edgecolor='white', cmap=cmap, vmin=avg_participation - 24, vmax= avg_participation + 24)
map_canton.plot(ax=ax, linewidth=3.5, edgecolor='black', color=(0, 0, 0, 0)) # Thicker canton borders

# Disable all ticks
ax.tick_params(which='both', bottom=False, top=False, right=False, left=False, labelleft=False, labelbottom=False) 

# Disable all spines
ax.spines.bottom.set_visible(False)
ax.spines.top.set_visible(False)
ax.spines.left.set_visible(False)
ax.spines.right.set_visible(False)

# Make annotations
do_annotations(ax)

# Draw the legend
f.legend(handles=legend_elements_negative, bbox_to_anchor=(0.3205, 0.85), **legend_kwargs)
f.legend(handles=legend_elements_positive, bbox_to_anchor=(0.2605, 0.85), **legend_kwargs)

# Set title
f.suptitle('Voter Participation on Municipality Level', fontproperties={'family': 'Jost', 'size': 60, 'weight': 'bold'}, x=0.37, y=0.9)

# Set subtitle (there might be a better way, but I could not find a way to have differently colored text in one object...)
f.text(x=0.157, y=0.85, s=f"Difference —              and               — in voter participation, compared to the", 
       color='dimgrey', fontproperties={'family': 'Jost', 'size': 27, 'weight': 'regular'})
f.text(x=0.2181, y=0.85, s="positive", color='#e66101', fontproperties={'family': 'Jost', 'size': 27, 'weight': 'semibold'})
f.text(x=0.2782, y=0.85, s="negative", color='#5e3c99', fontproperties={'family': 'Jost', 'size': 27, 'weight': 'semibold'})
f.text(x=0.508, y=0.85, s=f"Swiss average of {avg_participation:.1f}%", color='black', fontproperties={'family': 'Jost', 'size': 27, 'weight': 'semibold'})

# Set sources
f.text(x=0.8, y=0.175, s="Sources: bfs.admin.ch", color='dimgrey', fontproperties={'family': 'Jost', 'size': 18, 'weight': 'semibold'})

# Save the figure
plt.savefig('build/voter_participation_community.png', bbox_inches='tight', pad_inches=0.5)

c:\git\data-visualizations\.env3\lib\site-packages\matplotlib\text.py:1461: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  x = float(self.convert_xunits(x))
c:\git\data-visualizations\.env3\lib\site-packages\matplotlib\text.py:1463: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  y = float(self.convert_yunits(y))
